# COMPASS Model Diagnostics 2: Electric Bogaloo

A number of plots are provided from ADF. The full output from the stand-alone ADF configuration is in the link below.


Note that in standalone format (eg, CUPiD run not through CESM workflow), ADF is currently run by users via the following process:
1) Install ADF and activate cupid-analysis
2) Use the `CUPiD/helper_scripts/generate_adf_config_file.py` script to generate an ADF config file based on a CUPiD configuration file.
   * `cd CUPiD/examples/external_diag_packages`
   * `../../helper_scripts/generate_adf_config_file.py --cupid-config-loc . --adf-template ../../externals/ADF/config_amwg_default_plots.yaml --out-file ADF_config.yaml`
3) Run ADF with the newly created configuration file.
   * `../../externals/ADF/run_adf_diag ADF_config.yaml`

In [1]:
adf_root = "."
case_name = None
base_case_name = None
start_date = ""
end_date = ""
base_start_date = None
base_end_date = None
key_plots = None
compare_obs = False
var_list = ["T"]
compass_root = "."
runs_dict = {}

# adf_root will be external_diag_packages/computed_notebooks/ADF/

In [2]:
# Parameters
case_name = "b.e23_alpha17f.BLT1850.ne30_t232.092"
base_case_name = "b.e30_beta02.BLT1850.ne30_t232.104"
case_nickname = "BLT1850_92"
base_case_nickname = "BLT1850_104"
CESM_output_dir = "/glade/campaign/cesm/development/cross-wg/diagnostic_framework/CESM_output_for_testing"
start_date = "0001-01-01"
end_date = "0021-01-01"
climo_start_date = "0001-01-01"
climo_end_date = "0021-01-01"
base_start_date = "0001-01-01"
base_end_date = "0045-01-01"
base_climo_start_date = "0001-01-01"
base_climo_end_date = "0021-01-01"
obs_data_dir = (
    "/glade/campaign/cesm/development/cross-wg/diagnostic_framework/CUPiD_obs_data"
)
ts_dir = None
lc_kwargs = {"threads_per_worker": 1}
serial = False
compass_root = "/glade/work/richling/ADF/ADF_dev/Justin_ADF_2/ADF/adf_try_plots/f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull/T/ERA5/RF13/"
runs_dict = {
    "f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull": [
        "f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_tau12h.001",
        "f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_tau24h.001",
    ],
    "f.e30_cam6_4_120.FHISTC_LTso.ne30pg3_ne30pg3_mg17.SOCRATES_nudgeUVTfull_withCOSP": [
        "f.e30_cam6_4_120.FHISTC_LTso.ne30pg3_ne30pg3_mg17.SOCRATES_nudgeUVTfull_withCOSP_tau6h.001",
        "f.e30_cam6_4_120.FHISTC_LTso.ne30pg3_ne30pg3_mg17.SOCRATES_nudgeUVTfull_withCOSP_tau12h.001",
    ],
}
subset_kwargs = {}
product = "/glade/derecho/scratch/richling/compass-cupid/CUPiD/examples/external_diag_packages/computed_notebooks//atm/COMPASS_model_diags_2.ipynb"


In [3]:
runs_dict_tmp = {}
if isinstance(runs_dict, list):
    for run in runs_dict:
        runs_dict_tmp[run] = [run]
    runs_dict = runs_dict_tmp

## Key Metrics from COMPASS Model Diagnostics (CMD)

Some important things to look at from CMD include a slap to the face and then a hug:

for path_to_key_plot in key_plots:
    full_path = os.path.join(adf_root, path_to_key_plot)
    if os.path.isfile(full_path):
        display(Image(full_pbath))

In [4]:
def slider(case_name, image_dir, ldrop=None, settings_list=None, rdrop=None):
    import os
    import re
    from glob import glob
    from PIL import Image
    from io import BytesIO
    import base64
    from IPython.display import display, HTML
    import ipywidgets as widgets
    from ipywidgets import Layout

    tooltip_dict = {
        "Nudge_Uprof": """Selectively apply nudging to U:

        OFF = Switch off nudging
        ON = Apply nudging everywhere
        WINDOW = Apply window function to
        nudging tendencies.
        
        0 = OFF
        1 = ON
        2 = WINDOW
        """,
        #"nudge_uprof": "Profile of zonal wind nudging",
        "Nudge_Ucoef": """Selectively adjust the nudging strength applied to U. (normalized) [0.,1.]
        """,
        "Nudge_Hwin_lat0": """Specify the horizontal center of the
        window (lat0) in degrees. [-90., +90.]""",
                "Nudge_Hwin_lon0":"""Specify the horizontal center of the
        window (lon0) in degrees. [ 0. , 360.]""",
                "Nudge_Hwin_latWidth": """Specify the lat width of the
        horizontal window in degrees.
        Setting a width to a large value
        (e.g. 999.) renders the window
        constant in that direction.
        
        >0""",
                "Nudge_Hwin_lonWidth": """Specify the lon width of the
        horizontal window in degrees.
        Setting a width to a large value
        (e.g. 999.) renders the window
        constant in that direction.
        
        >0""",
        "Nudge_Vwin_Hindex": "Vertical window high index",
        "Nudge_Vwin_Lindex": "Vertical window low index",
        "Nudge_Vwin_Hdelta": "Vertical window high delta",
        "Nudge_Vwin_Ldelta": "Vertical window low delta",
        "Nudge_Vwin_Invert":"""A logical flag used to invert the
        horizontal window function to get its
        compliment.
        
        True/False""",
                "Nudge_Hwin_latDelta": "Horizontal lat delta",
                "Nudge_Hwin_lonDelta": "Horizontal lon delta",
                "Nudge_Hwin_Invert":"""A logical flag used to invert the
        horizontal window function to get its
        compliment.
        (e.g. to nudge outside a given window)
        
        True/False""",
    "Nudge_TimeScale_Opt":"""Select the timescale for the relaxation:

            WEAK = Constant time scale based in
            the time interval of Target values.
            
            STRONG = Variable timescale which
            gets stronger near each Target time.
            
            0 = WEAK
            1 = STRONG
            """,
    "Nudge_Force_Opt":"""Select the form of the Target values:

        NEXT = Target at next future time
        LINEAR = Linearly interpolate Target
        values to current model time.

        0 = NEXT
        1 = LINEAR
    """
    }


    link_dict = {
        "Nudge_Uprof": "https://ncar.github.io/CAM/doc/build/html/users_guide/physics-modifications-via-the-namelist.html?highlight=nudge#namelist-values",
        "Nudge_Ucoef": "https://ncar.github.io/CAM/doc/build/html/users_guide/physics-modifications-via-the-namelist.html?highlight=nudge#namelist-values",
        "Nudge_TimeScale_Opt":"www.google.com",
        #"nudge_timescale_opt":"www.google.com"
    }

    if not image_dir:
        print("No image directory :/")
        return

    # --- Detect levels ---
    lev_pattern = re.compile(r'(\d+)hPa\.png$')
    all_files = os.listdir(image_dir)
    levels = sorted({lev_pattern.search(f).group(1) for f in all_files if lev_pattern.search(f)})

    if not levels:
        print("No level-specific image files found.")
        return

    # Grab all PNG files
    files = glob(os.path.join(image_dir, "*.png"))

    # Regex to extract timestamp after hPa_ and before .png
    timestamp_pattern = re.compile(r"hPa_(\d{4}_\d{2}_\d{2}_\d{2}:\d{2})\.png$")

    timestamps = []
    for f in all_files:
        base = os.path.basename(f)
        m = timestamp_pattern.search(base)
        if m:
            timestamps.append(m.group(1))

    # Optional: sort by timestamp
    timestamps = sorted(timestamps)
    print(timestamps)
    # Widgets
    level_dropdown = widgets.Dropdown(options=levels, value=levels[0], description="Level (hPa)")
    slider = widgets.IntSlider(min=0, max=0, step=1, description='Time Step')
    #time_label = widgets.Label(value=str(timestamps[0]))
    #def update_label(change):
    #    time_label.value = timestamps[slider.value].strftime("%Y-%m-%d %H:%M")
    html_widget = widgets.HTML()

    def get_images_for_level(level):
        level = str(level)
        level_files = sorted([
            os.path.join(image_dir, f) for f in os.listdir(image_dir)
            if f.endswith(f'{level}hPa.png')
        ])
        timestamps = [
            '-'.join(os.path.basename(f).split('_')[1:4]) + ' ' + os.path.basename(f).split('_')[4]
            for f in level_files
        ]
        return level_files, timestamps

    image_files, timestamps = get_images_for_level(levels[0])
    print(timestamps)
    #image_files = get_images_for_level(levels[0])
    slider.max = max(0, len(image_files) - 1)

    def image_to_html(path):
        img = Image.open(path).resize((1000, 300))
        buffer = BytesIO()
        img.save(buffer, format='PNG')
        b64 = base64.b64encode(buffer.getvalue()).decode()
        return f"<img src='data:image/png;base64,{b64}' style='width:100%;'/>"

    def update_display(change=None):
        if not image_files:
            html_widget.value = "<b>No images found for this level.</b>"
            return
        html_img = image_to_html(image_files[slider.value])
        html_ts = f"<h3 style='text-align:center;'>{timestamps[slider.value]}</h3>"
        html_widget.value = html_ts + html_img

    def on_level_change(change):
        nonlocal image_files, timestamps
        image_files, timestamps = get_images_for_level(change.new)
        slider.max = max(0, len(image_files) - 1)
        slider.value = 0
        update_display()

    # --- Case info ---
    def load_user_nl(ldrop, settings_list):
        default_setting_list = ["fincl","mfilt","nhtfrq","ncdata"]
        #if isinstance(ldrop,list):
        lines_nudged = []
        lines_all = []
        lines_subset = []
        try:
            with open(ldrop, 'r') as file:
                for line in file:
                    if line.startswith(' Nudge_') or line.startswith(' nudge_') or line.startswith('Nudge_') or line.startswith('nudge_'):
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                        lines_nudged.append(cleaned_line.strip())
                    #if line.startswith('fincl2'):
                    if settings_list:
                        for setting in settings_list:
                            if setting not in default_setting_list:
                                if setting in line:
                                    cleaned_line = re.sub(r'\s{3,}', ' ', line)
                                    lines_subset.append(cleaned_line.strip())
                    if "fincl" in line:
                        #print("non")
                        strp_line = line.strip()
                        #print(strp_line)
                        cleaned_line = re.sub(r'\s{3,}', ' ', strp_line)
                        #print("cleaned")
                        #print(cleaned_line)
                        lines_subset.append(cleaned_line)
                    if "mfilt" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                    if "nhtfrq" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                    if "ncdata" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                    lines_all.append(line.strip())
        except Exception as e:
            lines = [f"Error reading user_nl_cam: {e}"]
            lines_all = lines
        return "\n".join(lines_nudged), "\n".join(lines_all), "\n".join(lines_subset)

    def load_case_status(case_status):
        lines = []
        try:
            with open(case_status, 'r') as file:
                #cleaned_line = re.sub(r'\s{3,}', ' ', line)
                #lines_all.append(cleaned_line.strip())
                lines = [re.sub(r'\s{3,}', ' ', line).strip() for line in file]
                #lines = [line.strip() for line in file]
        except Exception as e:
            lines = [f"Error reading CaseStatus: {e}"]
        return "\n".join(lines)

    ldrop_opts=["Hide Settings", "Nudge Params"]
    # "Nudge Params", "Full user_nl_cam"
    if ldrop:
        nudge_text, full_text, subset_text = load_user_nl(ldrop,settings_list)
        #print(full_text)
        fname = ""
        if "atm_in" in ldrop:
            ldrop_opts.append("Full atm_in")
            ldrop_opts.append("Subset atm_in")
            fname = "atm_in"
        if "user_nl_cam" in ldrop:
            ldrop_opts.append("Full user_nl_cam")
            fname = "user_nl_cam"
    if rdrop:
        status_text = load_case_status(rdrop)
        #print("status_text",status_text)
    else:
        status_text  = "Nothing here..."
    
    #settings_dropdown = widgets.Dropdown(options=["Hide Settings", "Nudge Params", "Full user_nl_cam"], description="Settings")
    #status_dropdown = widgets.Dropdown(options=["Hide CaseStatus", "CaseStatus"], description="CaseDocs")

    settings_dropdown = widgets.Dropdown(options=ldrop_opts, description="Settings")
    status_dropdown = widgets.Dropdown(options=["Hide CaseStatus", "CaseStatus"], description="CaseDocs")
    
    settings_output = widgets.Output()
    status_output = widgets.Output()

    import re
    from IPython.display import HTML
    
    def update_settings(change):
        settings_output.clear_output()
        if settings_dropdown.value == "Nudge Params":
            processed_lines = []
    
            for line in nudge_text.splitlines():
                original_line = line  # Keep the original for searchability
    
                for key in tooltip_dict.keys():
                    # Case-insensitive replacement
                    pattern = re.compile(re.escape(key), re.IGNORECASE)
                    title = tooltip_dict.get(key, "")
                    href = link_dict.get(key, "")
    
                    if href:
                        replacement = f'<a href="{href}" target="_blank" title="{title}">{key}</a>'
                    else:
                        replacement = f'<span title="{title}">{key}</span>'
    
                    line = pattern.sub(replacement, line)
    
                # Wrap the line in <div> and preserve the original line in a hidden <pre> for search
                processed_lines.append(line)
    
            html_output = "<br>".join(processed_lines)
    
            with settings_output:
                # Use <pre> + HTML for easy copy/search
                display(HTML(f"<pre style='white-space: pre-wrap; font-family: monospace;'>{html_output}</pre>"))
    
        elif settings_dropdown.value == f"Subset {fname}":
            with settings_output:
                display(HTML(f"<pre style='white-space: pre-wrap;'>{subset_text}</pre>"))
        elif settings_dropdown.value == f"Full {fname}":
            with settings_output:
                display(HTML(f"<pre style='white-space: pre-wrap;'>{full_text}</pre>"))

    
    
    
    """
    def update_settings(change):
        settings_output.clear_output()
        if settings_dropdown.value == "Nudge Params":
            processed_lines = []
            for line in nudge_text.splitlines():
                #for key in set(link_dict.keys()).union(tooltip_dict.keys()): #use as an intersection of both dict kyes
                for key in tooltip_dict.keys():
                    #match = next((k for k in tooltip_dict if k.upper() == key.upper()), None)
                    #if k.upper() == key
                    if key.lower() in line:
                        title = tooltip_dict.get(key, "")
                        href = link_dict.get(key, "")
                        if href:
                            replacement = f'<a href="{href}" target="_blank" title="{title}">{key.lower()}</a>'
                        else:
                            replacement = f'<span title="{title}">{key.lower()}</span>'
                        line = line.replace(key.lower(), replacement)
                processed_lines.append(line)
            html_output = "<br>".join(processed_lines)
            with settings_output:
                display(HTML(html_output))
        elif settings_dropdown.value == f"Subset {fname}":
            with settings_output:
                display(HTML("<pre>" + subset_text + "</pre>"))
        elif settings_dropdown.value == f"Full {fname}":
            with settings_output:
                display(HTML("<pre>" + full_text + "</pre>"))
    """

    def update_status(change):
        with status_output:
            status_output.clear_output()
            if status_dropdown.value == "CaseStatus":
                print(status_text)

    slider.observe(update_display, names='value')
    settings_dropdown.observe(update_settings, names='value')
    status_dropdown.observe(update_status, names='value')
    level_dropdown.observe(on_level_change, names='value')

    # Layout
    settings_output.layout = Layout(margin='0 20px 0 0')
    status_output.layout = Layout(margin='0 0 0 20px')
    output_row = widgets.HBox([settings_output, status_output])
    dropdown_row = widgets.HBox([settings_dropdown, status_dropdown], layout=Layout(margin='10px 0 10px 0'))
    control_row = widgets.HBox([level_dropdown, slider])
    title = widgets.HTML(
        value=f"<h4 style='text-align:center; margin:5px 5px;'>{case_name}</h4>"
    )
    ui = widgets.VBox([title, control_row, html_widget, dropdown_row, output_row])

    #display(ui)
    #update_display()

    update_display()
    return ui


In [5]:
import ipywidgets as widgets
from IPython.display import display
from pathlib import Path

# ----------------------------------------------------------
# Define your case *families* and runs
# ----------------------------------------------------------
case_groups = {
    "f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull": [
        "f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_tau12h.001",
        "f.e21.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_tau24h.001",
    ],
    "f.e30_cam6_4_120.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_withCOSP": [
        "f.e30_cam6_4_120.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_withCOSP_tau6h.001",
        #"f.e30_cam6_4_120.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_withCOSP_tau48h.001",
    ]
}

# ----------------------------------------------------------
# Create nested tabs
# ----------------------------------------------------------
top_tabs = widgets.Tab()

top_level_children = []
top_titles = []
for var in var_list:
    plot_type = "T"
    #file_path = Path(f"/glade/derecho/scratch/islas/{caze}/run/atm_in")
for case_family, run_list in case_groups.items():

    # Create sub-tab for each family
    sub_tab = widgets.Tab()

    sub_children = []
    sub_titles = []

    for run in run_list:
        # Replace this with: widget = slider(...)
        #widget = fake_slider(run)
        #caze = "f.e30_cam6_4_120.FHIST_BGC.f09_f09_mg17.SOCRATES_nudgeUVTfull_withCOSP_tau6h.001"
        file_path = Path(f"/glade/derecho/scratch/islas/{run}/run/atm_in")
        widget = slider(run,
                #f"plots/{run}/{plot_type}/ERA5/RF13/",
                compass_root,
               f"{str(file_path)}",
              #settings_list=["fincl","mfilt","nhtfrq","ncdata","cld","cosp"],
                settings_list=["cosp"],
            #rdrop="/glade/derecho/scratch/richling/cases/F2000climo.f09_f09_mg17.window.exp.6hrInit.R13.003/CaseStatus"
        )

        sub_children.append(widget)
        sub_titles.append(run)

    sub_tab.children = sub_children

    # Name the sub-tabs (each run)
    for i, title in enumerate(sub_titles):
        sub_tab.set_title(i, title)

    # Add subtab into top tab
    top_level_children.append(sub_tab)
    top_titles.append(case_family)

# Assign to top-level tab
top_tabs.children = top_level_children

# Name top-level tabs (each case family)
for i, title in enumerate(top_titles):
    top_tabs.set_title(i, title)

display(top_tabs)


[]
['2018-02-19 17:00', '2018-02-19 18:00', '2018-02-19 19:00', '2018-02-19 20:00', '2018-02-19 21:00', '2018-02-19 22:00', '2018-02-19 23:00', '2018-02-20 00:00', '2018-02-20 01:00', '2018-02-20 02:00', '2018-02-20 03:00', '2018-02-20 04:00', '2018-02-20 05:00', '2018-02-20 06:00', '2018-02-20 07:00']
[]
['2018-02-19 17:00', '2018-02-19 18:00', '2018-02-19 19:00', '2018-02-19 20:00', '2018-02-19 21:00', '2018-02-19 22:00', '2018-02-19 23:00', '2018-02-20 00:00', '2018-02-20 01:00', '2018-02-20 02:00', '2018-02-20 03:00', '2018-02-20 04:00', '2018-02-20 05:00', '2018-02-20 06:00', '2018-02-20 07:00']
[]
['2018-02-19 17:00', '2018-02-19 18:00', '2018-02-19 19:00', '2018-02-19 20:00', '2018-02-19 21:00', '2018-02-19 22:00', '2018-02-19 23:00', '2018-02-20 00:00', '2018-02-20 01:00', '2018-02-20 02:00', '2018-02-20 03:00', '2018-02-20 04:00', '2018-02-20 05:00', '2018-02-20 06:00', '2018-02-20 07:00']


In [6]:
#GOOD FUNCTION
from IPython.display import HTML, display
import os, re, json
from glob import glob
from PIL import Image
from io import BytesIO
import base64
from html import escape

def build_slider_html(case_name, image_dir, ldrop=None, settings_list=None, rdrop=None):
    """
    Convert your slider(...) to a pure HTML/CSS/JS blob returned as IPython.display.HTML.
    - case_name: string
    - image_dir: directory containing images named like ..._<level>hPa.png and with timestamps after 'hPa_'
    - ldrop: path to user_nl (optional)
    - settings_list: list of additional keywords to include in subset (optional)
    - rdrop: path to CaseStatus (optional)
    """
    # --- tooltip / link dicts from your function ---
    tooltip_dict = {
        "Nudge_Uprof": """Selectively apply nudging to U:

OFF = Switch off nudging
ON = Apply nudging everywhere
WINDOW = Apply window function to
nudging tendencies.

0 = OFF
1 = ON
2 = WINDOW
""",
        "Nudge_Ucoef": "Selectively adjust the nudging strength applied to U. (normalized) [0.,1.]",
        "Nudge_Hwin_lat0": "Specify the horizontal center of the window (lat0) in degrees. [-90., +90.]",
        "Nudge_Hwin_lon0": "Specify the horizontal center of the window (lon0) in degrees. [ 0. , 360.]",
        "Nudge_Hwin_latWidth": "Specify the lat width of the horizontal window in degrees. >0",
        "Nudge_Hwin_lonWidth": "Specify the lon width of the horizontal window in degrees. >0",
        "Nudge_Vwin_Hindex": "Vertical window high index",
        "Nudge_Vwin_Lindex": "Vertical window low index",
        "Nudge_Vwin_Hdelta": "Vertical window high delta",
        "Nudge_Vwin_Ldelta": "Vertical window low delta",
        "Nudge_Vwin_Invert": "A logical flag used to invert the horizontal window function to get its compliment. True/False",
        "Nudge_Hwin_latDelta": "Horizontal lat delta",
        "Nudge_Hwin_lonDelta": "Horizontal lon delta",
        "Nudge_Hwin_Invert": "A logical flag used to invert the horizontal window function to get its compliment. (e.g. to nudge outside a given window) True/False",
        "Nudge_TimeScale_Opt": "Select the timescale for the relaxation: WEAK / STRONG (0=WEAK,1=STRONG)",
        "Nudge_Force_Opt": "Select the form of the Target values: NEXT / LINEAR (0=NEXT,1=LINEAR)"
    }

    link_dict = {
        "Nudge_Uprof": "https://ncar.github.io/CAM/doc/build/html/users_guide/physics-modifications-via-the-namelist.html?highlight=nudge#namelist-values",
        "Nudge_Ucoef": "https://ncar.github.io/CAM/doc/build/html/users_guide/physics-modifications-via-the-namelist.html?highlight=nudge#namelist-values",
        "Nudge_TimeScale_Opt": "https://www.google.com"
    }

    # --- guard ---
    if not image_dir or not os.path.isdir(image_dir):
        return HTML(f"<div style='color:red;'>No valid image_dir: {escape(str(image_dir))}</div>")

    # --- detect levels and image files per level ---
    lev_pattern = re.compile(r'(\d+)hPa\.png$')
    all_files = os.listdir(image_dir)
    levels = sorted({lev_pattern.search(f).group(1) for f in all_files if lev_pattern.search(f)})
    if not levels:
        return HTML("<div style='color:red;'>No level-specific image files found (expecting '*hPa.png').</div>")

    # helper to extract timestamp like your original code
    timestamp_pattern = re.compile(r"hPa_(\d{4}_\d{2}_\d{2}_\d{2}:\d{2})\.png$")

    def get_images_for_level(level):
        level = str(level)
        level_files = sorted([
            os.path.join(image_dir, f) for f in os.listdir(image_dir)
            if f.endswith(f'{level}hPa.png')
        ])
        timestamps = [
            '-'.join(os.path.basename(f).split('_')[1:4]) + ' ' + os.path.basename(f).split('_')[4]
            for f in level_files
        ]
        return level_files, timestamps

    # --- build base64-encoded images per level (list of lists) ---
    images_per_level = {}
    timestamps_per_level = {}
    for lev in levels:
        files, tss = get_images_for_level(lev)
        b64_list = []
        for p in files:
            try:
                img = Image.open(p)
                # keep aspect similar to your original resize (1000x300) but scale if smaller
                #img = img.resize((1000, 300))
                img = img.resize((1200, 400))
                buf = BytesIO()
                img.save(buf, format='PNG')
                b64 = base64.b64encode(buf.getvalue()).decode()
                b64_list.append(b64)
            except Exception as e:
                b64_list.append("")  # placeholder if something fails
        images_per_level[lev] = b64_list
        timestamps_per_level[lev] = tss

    # --- load and process settings and status text like your original functions ---
    def load_user_nl(ldrop, settings_list):
        default_setting_list = ["fincl","mfilt","nhtfrq","ncdata"]
        lines_nudged = []
        lines_all = []
        lines_subset = []
        try:
            with open(ldrop, 'r') as file:
                for line in file:
                    if line.startswith(' Nudge_') or line.startswith(' nudge_') or line.startswith('Nudge_') or line.startswith('nudge_'):
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                        lines_nudged.append(cleaned_line.strip())
                    if settings_list:
                        for setting in settings_list:
                            if setting not in default_setting_list:
                                if setting in line:
                                    cleaned_line = re.sub(r'\s{3,}', ' ', line)
                                    lines_subset.append(cleaned_line.strip())
                    if "fincl" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line.strip())
                        lines_subset.append(cleaned_line)
                    if "mfilt" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                    if "nhtfrq" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                    if "ncdata" in line:
                        cleaned_line = re.sub(r'\s{3,}', ' ', line)
                        lines_subset.append(cleaned_line.strip())
                    lines_all.append(line.strip())
        except Exception as e:
            lines_all = [f"Error reading user_nl_cam: {e}"]
        return "\n".join(lines_nudged), "\n".join(lines_all), "\n".join(lines_subset)

    def load_case_status(case_status):
        lines = []
        try:
            with open(case_status, 'r') as file:
                lines = [re.sub(r'\s{3,}', ' ', line).strip() for line in file]
        except Exception as e:
            lines = [f"Error reading CaseStatus: {e}"]
        return "\n".join(lines)

    ldrop_opts = ["Hide Settings", "Nudge Params"]
    fname = ""
    nudge_text = full_text = subset_text = ""
    if ldrop and os.path.isfile(ldrop):
        nudge_text, full_text, subset_text = load_user_nl(ldrop, settings_list)
        if "atm_in" in ldrop:
            ldrop_opts += ["Full atm_in", "Subset atm_in"]
            fname = "atm_in"
        if "user_nl_cam" in ldrop:
            ldrop_opts.append("Full user_nl_cam")
            fname = "user_nl_cam"

    if rdrop and os.path.isfile(rdrop):
        status_text = load_case_status(rdrop)
    else:
        status_text = "Nothing here..."

    # --- sanitized HTML snippets ready for insertion (escape content except where we want HTML links) ---
    # For settings Nudge Params we will replace keys with <a> or <span> including title attributes.
    def process_nudge_html(text):
        lines = []
        for line in text.splitlines():
            original = line
            for key in tooltip_dict.keys():
                pattern = re.compile(re.escape(key), re.IGNORECASE)
                title = tooltip_dict.get(key, "")
                href = link_dict.get(key, "")
                if href:
                    repl = f'<a href="{href}" target="_blank" title="{escape(title)}">{escape(key)}</a>'
                else:
                    repl = f'<span title="{escape(title)}">{escape(key)}</span>'
                line = pattern.sub(repl, line)
            # escape leftover content
            # we assume replacements already escaped; ensure any other characters are safe
            lines.append(escape(line, quote=False))
        # join with <br> and then unescape the already-constructed <a>/<span> by replacing their escaped forms
        html_out = "<br>".join(lines)
        # fix the escaped <a> and <span> by unescaping their tags (they were double-escaped)
        # (we purposely escaped the full line earlier — now restore tags)
        for key in tooltip_dict.keys():
            # replace the escaped anchor/span (they contain &lt;a ... &gt;) with actual tags by searching for the escaped substring
            if key in html_out:
                # anchors contain the key text; replace the escaped key-only instances with unescaped link/span
                # This step is conservative and will mainly restore our inserted tags.
                pass
        # simpler: since we already constructed repl with proper tags and then escaped the whole line,
        # we need to instead rebuild from original again but carefully:
        processed = []
        for line in text.splitlines():
            line2 = line
            for key in tooltip_dict.keys():
                pattern = re.compile(re.escape(key), re.IGNORECASE)
                title = tooltip_dict.get(key, "")
                href = link_dict.get(key, "")
                if href:
                    repl = f'<a href="{href}" target="_blank" title="{escape(title)}">{escape(key)}</a>'
                else:
                    repl = f'<span title="{escape(title)}">{escape(key)}</span>'
                line2 = pattern.sub(repl, line2)
            processed.append(escape(line2))
        # Now processed contains escaped content with tags escaped; we must insert the tags verbatim.
        # So we'll take the original lines and perform the substitution without escaping the replacements.
        final_lines = []
        for line in text.splitlines():
            ln = line
            for key in tooltip_dict.keys():
                pattern = re.compile(re.escape(key), re.IGNORECASE)
                title = tooltip_dict.get(key, "")
                href = link_dict.get(key, "")
                if href:
                    repl = f'<a href="{href}" target="_blank" title="{escape(title)}">{escape(key)}</a>'
                else:
                    repl = f'<span title="{escape(title)}">{escape(key)}</span>'
                ln = pattern.sub(repl, ln)
            final_lines.append(escape(ln))
        # convert to HTML with <pre> styling preserved
        return "<pre style='white-space: pre-wrap; font-family: monospace;'>" + "<br>".join(final_lines) + "</pre>"

    nudge_html = process_nudge_html(nudge_text) if nudge_text else "<div><em>No nudge params found.</em></div>"
    subset_html = "<pre style='white-space: pre-wrap; font-family: monospace;'>" + escape(subset_text) + "</pre>" if subset_text else "<div><em>No subset.</em></div>"
    full_html = "<pre style='white-space: pre-wrap; font-family: monospace;'>" + escape(full_text) + "</pre>" if full_text else "<div><em>No full text.</em></div>"
    status_html = "<pre style='white-space: pre-wrap; font-family: monospace;'>" + escape(status_text) + "</pre>"

    # --- Build an HTML blob and inject JSON data for JS ---
    data = {
        "case_name": case_name,
        "levels": levels,
        "images_per_level": images_per_level,
        "timestamps_per_level": timestamps_per_level,
        "nudge_html": nudge_html,
        "subset_html": subset_html,
        "full_html": full_html,
        "status_html": status_html,
        "ldrop_opts": ldrop_opts,
        "fname": fname
    }

    # Convert data to JSON safely for embedding
    data_json = json.dumps(data)

    # HTML/CSS/JS template
    html = f"""
<div class="cs-slider-root" style="font-family: Arial, Helvetica, sans-serif;">
  <style>
  .cs-title {{ text-align:center; margin:5px 5px; font-size:1.0rem; font-weight:600; }}
  .cs-controls {{ display:flex; gap:10px; align-items:center; justify-content:center; margin-bottom:10px; flex-wrap:wrap; }}
  .cs-controls select, .cs-controls input[type='range'] {{ font-size:0.95rem; padding:6px; }}
  .cs-image-wrap {{ width:100%; max-width:1200px; height:auto; border:1px solid #ddd; border-radius:4px; }}
  .cs-timestamp {{ text-align:center; font-weight:600; margin:6px 0; }}
  .cs-nav-buttons {{ display:flex; gap:6px; justify-content:center; margin-top:6px; }}
  .cs-small-btn {{ padding:6px 10px; cursor:pointer; border:1px solid #bbb; background:#f3f3f3; border-radius:4px; }}
  .cs-panels {{ display:flex; gap:20px; justify-content:center; flex-wrap:wrap; margin-top:12px; }}
  .cs-panel {{ width: 1200px; min-height: 120px; border:1px solid #ddd; padding:10px; background:#fafafa; border-radius:6px; }}
  .cs-panel pre {{ white-space: pre-wrap; font-family: monospace; font-size:0.9rem; }}
  .cs-label {{ font-weight:600; margin-right:6px; }}
  .cs-timestamp-list {{ display:flex; gap:6px; flex-wrap:wrap; justify-content:center; margin-top:8px; }}
  .cs-ts-btn {{ border:1px solid #ddd; padding:6px 8px; border-radius:4px; cursor:pointer; background:#fff; }}
  .cs-ts-btn.active {{ background:#e6f0ff; border-color:#7aa7ff; }}
  </style>

  <div class="cs-title">{escape(case_name)}</div>

  <div class="cs-controls" role="toolbar" aria-label="Controls">
    <label class="cs-label">Level:</label>
    <select id="cs-level-select"></select>

    <label class="cs-label">Time:</label>
    <input id="cs-slider-range" type="range" min="0" max="0" value="0" step="1" aria-label="time slider">
    <span id="cs-slider-index" style="min-width:120px; text-align:center; display:inline-block;"></span>
  </div>

  <div class="cs-image-wrap">
    <div id="cs-image-container" style="text-align:center;"></div>
    <div class="cs-nav-buttons">
      <button id="cs-prev" class="cs-small-btn">◀ Prev</button>
      <button id="cs-next" class="cs-small-btn">Next ▶</button>
    </div>
    <div id="cs-timestamp-list" class="cs-timestamp-list"></div>
  </div>

  <div class="cs-panels">
    <div class="cs-panel">
      <div style="display:flex; gap:8px; align-items:center; margin-bottom:8px;">
        <label class="cs-label">Settings:</label>
        <select id="cs-settings-select"></select>
      </div>
      <div id="cs-settings-content"><em>Choose Settings to view</em></div>
    </div>

    <div class="cs-panel">
      <div style="display:flex; gap:8px; align-items:center; margin-bottom:8px;">
        <label class="cs-label">CaseDocs:</label>
        <select id="cs-status-select">
          <option value="hide">Hide CaseStatus</option>
          <option value="show">CaseStatus</option>
        </select>
      </div>
      <div id="cs-status-content"><em>CaseStatus output</em></div>
    </div>
  </div>

</div>

<script>
(function() {{
  const data = {data_json};

  // DOM refs
  const levelSelect = document.getElementById('cs-level-select');
  const slider = document.getElementById('cs-slider-range');
  const sliderIndex = document.getElementById('cs-slider-index');
  const imageContainer = document.getElementById('cs-image-container');
  const prevBtn = document.getElementById('cs-prev');
  const nextBtn = document.getElementById('cs-next');
  const tsList = document.getElementById('cs-timestamp-list');
  const settingsSelect = document.getElementById('cs-settings-select');
  const settingsContent = document.getElementById('cs-settings-content');
  const statusSelect = document.getElementById('cs-status-select');
  const statusContent = document.getElementById('cs-status-content');

  // populate level select
  data.levels.forEach((lev,i) => {{
    const opt = document.createElement('option');
    opt.value = lev;
    opt.text = lev + " hPa";
    levelSelect.appendChild(opt);
  }});

  // populate settings select
  data.ldrop_opts.forEach(opt => {{
    const el = document.createElement('option');
    el.value = opt;
    el.text = opt;
    settingsSelect.appendChild(el);
  }});

  // initial state
  let curLevel = data.levels[0];
  let curIndex = 0;

  function renderImage() {{
    const b64 = data.images_per_level[curLevel][curIndex];
    const ts = data.timestamps_per_level[curLevel] && data.timestamps_per_level[curLevel][curIndex] ? data.timestamps_per_level[curLevel][curIndex] : "No timestamp";
    sliderIndex.innerHTML = `<strong>${{ts}}</strong>`;
    if (!b64) {{
      imageContainer.innerHTML = "<div style='color:#b00;'>Image missing or failed to load.</div>";
    }} else {{
      imageContainer.innerHTML = `<img src="data:image/png;base64,${{b64}}" style="width:100%; max-width:1000px; height:auto; border:1px solid #ddd; border-radius:4px;" />`;
    }}
    // update active timestamp button
    Array.from(tsList.children).forEach((btn, idx) => {{
      btn.classList.toggle('active', idx === curIndex);
    }});
    // sync slider
    slider.value = curIndex;
  }}

  function rebuildTimestampList() {{
    tsList.innerHTML = "";
    const tarr = data.timestamps_per_level[curLevel] || [];
    tarr.forEach((ts, i) => {{
      const b = document.createElement('button');
      b.className = 'cs-ts-btn';
      b.textContent = ts;
      b.onclick = () => {{
        curIndex = i;
        renderImage();
      }};
      tsList.appendChild(b);
    }});
  }}

  function setSliderMax() {{
    const n = (data.images_per_level[curLevel] || []).length;
    slider.max = Math.max(0, n - 1);
    if (curIndex > slider.max) curIndex = slider.max;
    slider.value = curIndex;
  }}

  // event handlers
  levelSelect.addEventListener('change', (e) => {{
    curLevel = e.target.value;
    curIndex = 0;
    setSliderMax();
    rebuildTimestampList();
    renderImage();
  }});

  slider.addEventListener('input', (e) => {{
    curIndex = parseInt(e.target.value);
    renderImage();
  }});

  prevBtn.addEventListener('click', () => {{
    curIndex = Math.max(0, curIndex - 1);
    renderImage();
  }});
  nextBtn.addEventListener('click', () => {{
    const maxv = parseInt(slider.max || 0);
    curIndex = Math.min(maxv, curIndex + 1);
    renderImage();
  }});

  // settings select behavior
  settingsSelect.addEventListener('change', (e) => {{
    const v = e.target.value;
    if (v === "Hide Settings") {{
      settingsContent.innerHTML = "<em>Hidden</em>";
    }} else if (v === "Nudge Params") {{
      settingsContent.innerHTML = data.nudge_html;
    }} else if (v.startsWith("Subset")) {{
      settingsContent.innerHTML = data.subset_html;
    }} else if (v.startsWith("Full")) {{
      settingsContent.innerHTML = data.full_html;
    }} else {{
      settingsContent.innerHTML = "<em>No data</em>";
    }}
  }});

  // status select behavior
  statusSelect.addEventListener('change', (e) => {{
    const v = e.target.value;
    if (v === "show") {{
      statusContent.innerHTML = data.status_html;
    }} else {{
      statusContent.innerHTML = "<em>Hidden</em>";
    }}
  }});

  // initialize UI
  setSliderMax();
  rebuildTimestampList();
  renderImage();
  // set initial selects (optional)
  settingsSelect.value = "Hide Settings";
  statusSelect.value = "hide";
}})();
</script>
    """

    return HTML(html)

In [7]:
#GOOD FUNCTION
from IPython.display import HTML, display
from pathlib import Path

outer_tabs_html = []
outer_tab_buttons = []
outer_content_html = []

for i, (outer_name, inner_runs) in enumerate(runs_dict.items()):
    # Outer tab button
    active_cls = "active" if i==0 else ""
    outer_tab_buttons.append(f'<div class="outer-tab {active_cls}" data-outer="outer{i}">{outer_name}</div>')

    inner_tabs = []
    inner_contents = []
    for j, run_name in enumerate(inner_runs):
        # Inner tab button
        inner_active = "active" if j==0 else ""
        inner_tabs.append(f'<div class="inner-tab {inner_active}" data-inner="inner{i}_{j}">{run_name.split("_")[-1]}</div>')

        ## Inner content: slider HTML
        #slider_html = build_slider_html(
        #    run_name,
        #    image_dir=f"/glade/derecho/scratch/islas/{run_name}/run/atm_in",
        #    settings_list=["cosp"],
        #).data  # get the raw HTML string
        file_path = Path(f"/glade/derecho/scratch/islas/{run_name}/run/atm_in")
        slider_html = build_slider_html(run_name,
                #f"plots/{run}/{plot_type}/ERA5/RF13/",
                compass_root,
               f"{str(file_path)}",
              #settings_list=["fincl","mfilt","nhtfrq","ncdata","cld","cosp"],
                settings_list=["cosp"],
            #rdrop="/glade/derecho/scratch/richling/cases/F2000climo.f09_f09_mg17.window.exp.6hrInit.R13.003/CaseStatus"
        ).data  # get the raw HTML string

        inner_contents.append(f'<div class="inner-content {inner_active}" id="inner{i}_{j}">{slider_html}</div>')

    outer_active = "active" if i==0 else ""
    outer_content_html.append(f"""
    <div class="outer-content {outer_active}" id="outer{i}">
        <div class="inner-tabs">{''.join(inner_tabs)}</div>
        {''.join(inner_contents)}
    </div>
    """)

html_full = f"""
<div class="outer-tabs">
{''.join(outer_tab_buttons)}
</div>
{''.join(outer_content_html)}

<style>
/* Outer / inner tab styles */
.outer-tabs {{ display:flex; cursor:pointer; margin-bottom:8px; }}
.outer-tab {{ padding:6px 12px; border:1px solid #ccc; margin-right:2px; border-radius:4px 4px 0 0; background:#eee; }}
.outer-tab.active {{ background:#fff; border-bottom:1px solid #fff; }}
.outer-content {{ border:1px solid #ccc; padding:6px; display:none; border-radius:0 4px 4px 4px; }}
.outer-content.active {{ display:block; }}

.inner-tabs {{ display:flex; cursor:pointer; margin-bottom:5px; }}
.inner-tab {{ padding:4px 10px; border:1px solid #ccc; margin-right:2px; border-radius:4px 4px 0 0; background:#ddd; }}
.inner-tab.active {{ background:#fff; border-bottom:1px solid #fff; }}
.inner-content {{ display:none; }}
.inner-content.active {{ display:block; }}
</style>

<script>
document.querySelectorAll('.outer-tab').forEach(tab => {{
    tab.addEventListener('click', () => {{
        document.querySelectorAll('.outer-tab').forEach(t => t.classList.remove('active'));
        document.querySelectorAll('.outer-content').forEach(c => c.classList.remove('active'));
        tab.classList.add('active');
        document.getElementById(tab.dataset.outer).classList.add('active');
    }});
}});

document.querySelectorAll('.inner-tabs').forEach(innerContainer => {{
    innerContainer.querySelectorAll('.inner-tab').forEach(tab => {{
        tab.addEventListener('click', () => {{
            innerContainer.querySelectorAll('.inner-tab').forEach(t => t.classList.remove('active'));
            innerContainer.parentElement.querySelectorAll('.inner-content').forEach(c => c.classList.remove('active'));
            tab.classList.add('active');
            document.getElementById(tab.dataset.inner).classList.add('active');
        }});
    }});
}});
</script>
"""



In [8]:
display(HTML(html_full))